In [ ]:
import pandas as pd
import numpy as np


def preprocess():
    
    # Open the file with the training data.
    file = ('houses.csv')
    df = pd.read_csv(file)
    
    #drop unneeded columns.
    df.drop(['Unnamed: 0','Furnished','Terrace orientation','Garden orientation','Number of facades']
            ,axis =1, inplace=True)
    
    # Clean data by narrowing down options, as to avoid to small sample sets disturbing the model.
        
        # Remove group sales of houses.
    df = df[df["Property type"]== "HOUSE"]
    
        # Simplify types of houses by redefining and removing
    df = df.replace({'Property subtype' : {'BUNGALOW':'HOUSE', 'TOWN_HOUSE': 'HOUSE', 'COUNTRY_COTTAGE': 'HOUSE',
                                           'CHALET':'HOUSE','COUNTRY_COTTAGE':'HOUSE'}}, regex=True)
    
    df = df[~df["Property subtype"].isin(["APARTMENT_BLOCK","CASTLE","EXCEPTIONAL_PROPERTY","HOUSE_GROUP",
                                          "OTHER_PROPERTY","MANOR_HOUSE"])]
    
        # We only want type of sale residential sale.
    df = df[df["Type of sale"]== "residential_sale"]
    
        # Some outliers with to many rooms or full apartment complexes with 50+ rooms and some houses with 0 bedrooms.
        # To avoid wrong results we limit the number of bedrooms
    df = df[(df["Number of bedrooms"]<10) & df["Number of bedrooms"]>0 ]
        
        # Some properties have land surfaces of 40000+m², removing these outliers and capping the max m².
    df = df[df["Surface area land"]< 5000]
        
        # Simplify if the kitchen is equipped with a simple yes/no
    df = df.replace({'Kitchen' : {'USA_HYPER_EQUIPPED':True,'USA_INSTALLED':True,'USA_SEMI_EQUIPPED':True,
                                  'USA_UNINSTALLED':False,'INSTALLED':True,'Unknown':False,'SEMI_EQUIPPED':False
                                  ,'HYPER_EQUIPPED':True,'NOT_INSTALLED':False, np.nan:False}}, regex=True)
        
        # Change unknowns to False for Terrace and Garden
    df = df.replace({'Terrace' : {'Unknown':'False'}}, regex=True)
    df = df.replace({'Garden' : {'Unknown':'False'}}, regex=True)
        
        # Change NaN to False for Pool.
    df = df.replace({'Pool' : {np.nan:'False'}}, regex=True)
        
        # Many types of conditions, some with the same meaning. Narrow it down to True = Good and False = To be renovated.
    df = df.replace({'Condition' : {'GOOD':False, 'AS_NEW':False, 'JUST_RENOVATED':False,'TO_RENOVATE': True, 
                                    'TO_BE_DONE_UP':True,'Unknown':True,'TO_RESTORE':True, np.nan:True, }}, regex=True)
        
        # Drop row in the following columns that have NaN's since we can't really replace it with a good guess.
    df.dropna(subset=['Price', 'Number of bedrooms','Living area'], inplace=True)
    
        # Our index is messed up so we reset it first.
    df.reset_index(inplace=True)
    
        # we change all the yes/no and True/False data we put in earlier to dummies.
    df = pd.get_dummies(df, columns=['Property subtype','Kitchen','Open fireplace','Terrace','Garden','Pool','Condition'])
    
        # We drop the columns that we don't need and all the False dummy columns.
    df.drop(['Property type','Type of sale','index','Kitchen_False','Open fireplace_False','Terrace_False','Garden_False','Pool_False','Condition_False'], axis =1, inplace=True)
    
        # We rename the True columns to look better.
    df.rename(columns= {'Kitchen_True':'Kitchen equipped','Open fireplace_True':'Open fireplace','Terrace_True':'Terrace','Garden_True':'Garden','Pool_True':'Pool','Condition_True':'Condition'}, inplace = True)

In [9]:
file = ('houses.csv')
df = pd.read_csv(file)
df.head()

Unnamed: 0   Location Property type Property subtype     Price  \
0           0   Verviers         HOUSE            HOUSE  296607.0   
1           1   Haasdonk         HOUSE            HOUSE  560000.0   
2           2      VIANE         HOUSE            HOUSE  299000.0   
3           3  Gerpinnes         HOUSE            HOUSE  300000.0   
4           4   Nivelles         HOUSE            HOUSE  195000.0   

       Type of sale  Number of bedrooms  Living area        Kitchen Furnished  \
0  residential_sale                 3.0        130.0        Unknown     False   
1  residential_sale                 4.0          NaN        Unknown       NaN   
2  residential_sale                 5.0        200.0  SEMI_EQUIPPED     False   
3  residential_sale                 0.0        270.0        Unknown     False   
4  residential_sale                 3.0        135.0      INSTALLED     False   

   Open fireplace  Terrace Terrace orientation   Garden Garden orientation  \
0           False     True             Unknown     True            Unknown   
1           False  Unknown             Unknown  Unknown            Unknown   
2           False  Unknown             Unknown  Unknown            Unknown   
3           False     True               SOUTH     True              SOUTH   
4           False     True             Unknown  Unknown            Unknown   

   Surface area land Number of facades   Pool Condition  
0              239.0                 3    NaN    AS_NEW  
1              626.0                 3    NaN    AS_NEW  
2             1150.0               NaN    NaN      GOOD  
3              498.0                 3  False       NaN  
4              165.0                 2  False       NaN

In [10]:
df.drop(['Unnamed: 0','Furnished','Terrace orientation','Garden orientation','Number of facades'], axis =1, inplace=True)
df.head()

Location Property type Property subtype     Price      Type of sale  \
0   Verviers         HOUSE            HOUSE  296607.0  residential_sale   
1   Haasdonk         HOUSE            HOUSE  560000.0  residential_sale   
2      VIANE         HOUSE            HOUSE  299000.0  residential_sale   
3  Gerpinnes         HOUSE            HOUSE  300000.0  residential_sale   
4   Nivelles         HOUSE            HOUSE  195000.0  residential_sale   

   Number of bedrooms  Living area        Kitchen  Open fireplace  Terrace  \
0                 3.0        130.0        Unknown           False     True   
1                 4.0          NaN        Unknown           False  Unknown   
2                 5.0        200.0  SEMI_EQUIPPED           False  Unknown   
3                 0.0        270.0        Unknown           False     True   
4                 3.0        135.0      INSTALLED           False     True   

    Garden  Surface area land   Pool Condition  
0     True              239.0    NaN    AS_NEW  
1  Unknown              626.0    NaN    AS_NEW  
2  Unknown             1150.0    NaN      GOOD  
3     True              498.0  False       NaN  
4  Unknown              165.0  False       NaN

In [11]:
df = df[df["Property type"]== "HOUSE"]

df = df.replace({'Property subtype' : {'BUNGALOW':'HOUSE', 'TOWN_HOUSE': 'HOUSE', 'COUNTRY_COTTAGE': 'HOUSE','CHALET':'HOUSE','COUNTRY_COTTAGE':'HOUSE'}}, regex=True)
df = df[~df["Property subtype"].isin(["APARTMENT_BLOCK","CASTLE","EXCEPTIONAL_PROPERTY","HOUSE_GROUP","OTHER_PROPERTY","MANOR_HOUSE"])]

df = df[df["Type of sale"]== "residential_sale"]
df = df[(df["Number of bedrooms"]<10) & df["Number of bedrooms"]>0 ]

df = df[df["Surface area land"]< 5000]

df = df.replace({'Kitchen' : {'USA_HYPER_EQUIPPED':True,'USA_INSTALLED':True,'USA_SEMI_EQUIPPED':True,'USA_UNINSTALLED':False,'INSTALLED':True,'Unknown':False,'SEMI_EQUIPPED':False,'HYPER_EQUIPPED':True,'NOT_INSTALLED':False, np.nan:False}}, regex=True)

df = df.replace({'Terrace' : {'Unknown':'False'}}, regex=True)
df = df.replace({'Garden' : {'Unknown':'False'}}, regex=True)

df = df.replace({'Pool' : {np.nan:'False'}}, regex=True)

# 1 means renovation needed
df = df.replace({'Condition' : {'GOOD':False, 'AS_NEW':False, 'JUST_RENOVATED':False,'TO_RENOVATE': True, 'TO_BE_DONE_UP':True,'Unknown':True,'TO_RESTORE':True, np.nan:True, }}, regex=True)

In [12]:
df.dropna(subset=['Price', 'Number of bedrooms','Living area'], inplace=True)

In [13]:
df.reset_index(inplace=True)
df = pd.get_dummies(df, columns=['Property subtype','Kitchen','Open fireplace','Terrace','Garden','Pool','Condition'])
df.drop(['Property type','Type of sale','index','Kitchen_False','Open fireplace_False','Terrace_False','Garden_False','Pool_False','Condition_False'], axis =1, inplace=True)
df.rename(columns= {'Kitchen_True':'Kitchen equipped','Open fireplace_True':'Open fireplace','Terrace_True':'Terrace','Garden_True':'Garden','Pool_True':'Pool','Condition_True':'Condition'}, inplace = True)

In [14]:
df

Location      Price  Number of bedrooms  Living area  \
0               Verviers   296607.0                 3.0        130.0   
1                  VIANE   299000.0                 5.0        200.0   
2               Nivelles   195000.0                 3.0        135.0   
3                 Dinant   175000.0                 3.0        128.0   
4                 Lierde   415000.0                 3.0        207.0   
...                  ...        ...                 ...          ...   
6883            Zaventem   488000.0                 3.0        150.0   
6884               Aalst   550000.0                 4.0       1380.0   
6885   Charleroi Ransart   115000.0                 2.0        120.0   
6886     Sars-la-Bruyère   280000.0                 3.0        120.0   
6887  Rhode-Saint-Genèse  1650000.0                 6.0        530.0   

      Surface area land  Property subtype_FARMHOUSE  Property subtype_HOUSE  \
0                 239.0                           0                       1   
1                1150.0                           0                       1   
2                 165.0                           0                       1   
3                 260.0                           0                       1   
4                 534.0                           0                       1   
...                 ...                         ...                     ...   
6883              390.0                           0                       1   
6884             1300.0                           0                       0   
6885              310.0                           0                       1   
6886              839.0                           0                       0   
6887             1400.0                           0                       0   

      Property subtype_MANSION  Property subtype_MIXED_USE_BUILDING  \
0                            0                                    0   
1                            0                                    0   
2                            0                                    0   
3                            0                                    0   
4                            0                                    0   
...                        ...                                  ...   
6883                         0                                    0   
6884                         0                                    0   
6885                         0                                    0   
6886                         0                                    0   
6887                         0                                    0   

      Property subtype_VILLA  Kitchen equipped  Open fireplace  Terrace  \
0                          0                 0               0        1   
1                          0                 0               0        0   
2                          0                 1               0        1   
3                          0                 1               0        1   
4                          0                 1               0        1   
...                      ...               ...             ...      ...   
6883                       0                 0               0        1   
6884                       1                 1               1        1   
6885                       0                 1               0        0   
6886                       1                 1               0        1   
6887                       1                 1               0        1   

      Garden  Pool  Condition  
0          1     0          0  
1          0     0          0  
2          0     0          1  
3          0     0          1  
4          1     0          0  
...      ...   ...        ...  
6883       1     0          0  
6884       1     0          0  
6885       1     0          1  
6886       1     0          0  
6887       1     1          0  

[6888 rows x 16 columns]

In [15]:
postcodes = pd.read_csv('postcodes_filtered.csv')
postcodes.head()

Postcode    Gemeente Deelgemeente                       Provincie  \
0    1000.0     Brussel          NaN  Brussels Hoofdstedelijk Gewest   
1    1000.0   Bruxelles          NaN  Brussels Hoofdstedelijk Gewest   
2    1030.0  Schaarbeek          NaN  Brussels Hoofdstedelijk Gewest   
3    1030.0  Schaerbeek          NaN  Brussels Hoofdstedelijk Gewest   
4    1040.0   Etterbeek          NaN  Brussels Hoofdstedelijk Gewest   

  deelgemeente  
0    Bruxelles  
1      Brussel  
2   Schaerbeek  
3   Schaarbeek  
4            -

In [16]:
count_yes =0
count_no =0

if city in df['Location'] == [postcodes['Gemeente'== city]]:
    print(city)
    print(place)
    count_yes+=1
else:
    count_no+=1
        
print(count_yes)
print(count_no)

NameError: name 'city' is not defined

In [ ]:
for index, row in df.iterrows():
    place = row['Location']
    print(place)
    for num, line in postcodes.iterrows():
        gemeente = line['Gemeente']
        print(gemeente)
        if place == gemeente:
            print('yes')
        else:
            print('no')
    

Verviers
Brussel
no
Bruxelles
no
Schaarbeek
no
Schaerbeek
no
Etterbeek
no
Elsene
no
Ixelles
no
Saint-Gilles
no
Sint-Gillis
no
Anderlecht
no
Molenbeek-Saint-Jean
no
Sint-Jans-Molenbeek
no
Koekelberg
no
Berchem-Sainte-Agathe
no
Sint-Agatha-Berchem
no
Ganshoren
no
Jette
no
Evere
no
Sint-Pieters-Woluwe
no
Woluwe-Saint-Pierre
no
Auderghem
no
Oudergem
no
Watermaal-Bosvoorde
no
Watermael-Boitsfort
no
Uccle
no
Ukkel
no
Forest
no
Vorst
no
Sint-Lambrechts-Woluwe
no
Woluwe-Saint-Lambert
no
Saint-Josse-ten-Noode
no
Sint-Joost-ten-Node
no
Wavre
no
Waver
no
La Hulpe
no
Terhulpen
no
Incourt
no
Beauvechain
no
Bevekom
no
Chaumont-Gistoux
no
Rixensart
no
Ottignies-Louvain-la-Neuve
no
Orp-Jauche
no
Hélécine
no
Perwez
no
Perwijs
no
Ramillies
no
Jodoigne
no
Geldenaken
no
Lasne
no
Grez-Doiceau
no
Graven
no
Nivelles
no
Nijvel
no
Waterloo
no
Braine-l'Alleud
no
Eigenbrakel
no
Rebecq
no
Mont-Saint-Guibert
no
Braine-le-Château
no
Kasteelbrakel
no
Chastre
no
Walhain
no
Ittre
no
Itter
no
Genappe
no
Genepiën
no
Tub

Burdinne
no
Burdinne
no
Héron
no
Héron
no
Héron
no
Wasseiges
no
Wasseiges
no
Wasseiges
no
Geer
no
Geer
no
Geer
no
Geer
no
Geer
no
Geer
no
Berloz
no
Berloz
no
Braives
no
Braives
no
Braives
no
Braives
no
Braives
no
Braives
no
Braives
no
Hannut
no
Hannut
no
Hannut
no
Hannut
no
Hannut
no
Hannut
no
Hannut
no
Hannut
no
Hannut
no
Hannut
no
Hannut
no
Hannut
no
Hannut
no
Hannut
no
Hannut
no
Hannut
no
Hannut
no
Lincent
no
Lincent
no
Waremme
no
Waremme
no
Waremme
no
Waremme
no
Waremme
no
Waremme
no
Faimes
no
Faimes
no
Faimes
no
Faimes
no
Faimes
no
Awans
no
Awans
no
Awans
no
Awans
no
Fexhe-le-Haut-Clocher
no
Fexhe-le-Haut-Clocher
no
Fexhe-le-Haut-Clocher
no
Fexhe-le-Haut-Clocher
no
Remicourt
no
Remicourt
no
Remicourt
no
Remicourt
no
Donceel
no
Donceel
no
Donceel
no
Oreye
no
Oreye
no
Oreye
no
Oreye
no
Crisnée
no
Crisnée
no
Crisnée
no
Crisnée
no
Flémalle
no
Flémalle
no
Flémalle
no
Flémalle
no
Flémalle
no
Flémalle
no
Flémalle
no
Saint-Nicolas
no
Saint-Nicolas
no
Ans
no
Ans
no
Ans
no
Juprelle
no
Jupre

no
Knokke-Heist
no
Knokke-Heist
no
Brugge
no
Brugge
no
Damme
no
Damme
no
Damme
no
Damme
no
Damme
no
Blankenberge
no
Zuienkerke
no
Zuienkerke
no
Zuienkerke
no
Brugge
no
Brugge
no
Oostende
no
Oostende
no
De Haan
no
De Haan
no
De Haan
no
Middelkerke
no
Middelkerke
no
Middelkerke
no
Middelkerke
no
Middelkerke
no
Middelkerke
no
Middelkerke
no
Middelkerke
no
Oudenburg
no
Oudenburg
no
Oudenburg
no
Gistel
no
Gistel
no
Gistel
no
Ichtegem
no
Ichtegem
no
Jabbeke
no
Jabbeke
no
Jabbeke
no
Jabbeke
no
Kortrijk
no
Kortrijk
no
Kortrijk
no
Kortrijk
no
Kortrijk
no
Kortrijk
no
Kortrijk
no
Harelbeke
no
Harelbeke
no
Zwevegem
no
Zwevegem
no
Zwevegem
no
Zwevegem
no
Wevelgem
no
Wevelgem
no
Anzegem
no
Anzegem
no
Anzegem
no
Anzegem
no
Anzegem
no
Avelgem
no
Avelgem
no
Avelgem
no
Avelgem
no
Espierres-Helchin
no
Espierres-Helchin
no
Spiere-Helkijn
no
Spiere-Helkijn
no
Diksmuide
no
Diksmuide
no
Diksmuide
no
Diksmuide
no
Diksmuide
no
Diksmuide
no
Diksmuide
no
Diksmuide
no
Diksmuide
no
Diksmuide
no
Diksmuide
no
Diksmu

no
Hasselt
no
Hasselt
no
Hasselt
no
Hasselt
no
Hasselt
no
Houthalen-Helchteren
no
Houthalen-Helchteren
no
Herk-de-Stad
no
Herk-de-Stad
no
Herk-de-Stad
no
Halen
no
Halen
no
Heusden-Zolder
no
Heusden-Zolder
no
Lummen
no
Lummen
no
Beringen
no
Beringen
no
Beringen
no
Lanaken
no
Lanaken
no
Lanaken
no
Lanaken
no
Maasmechelen
no
Maasmechelen
no
Maasmechelen
no
Maasmechelen
no
Maasmechelen
no
Maasmechelen
no
Maasmechelen
no
Maasmechelen
no
Kinrooi
no
Kinrooi
no
Kinrooi
no
Dilsen-Stokkem
no
Dilsen-Stokkem
no
Dilsen-Stokkem
no
Dilsen-Stokkem
no
Dilsen-Stokkem
no
As
no
Oudsbergen
no
Oudsbergen
no
Oudsbergen
no
Oudsbergen
no
Oudsbergen
no
Maaseik
no
Maaseik
no
Tongeren
no
Tongeren
no
Tongeren
no
Tongeren
no
Tongeren
no
Tongeren
no
Tongeren
no
Tongeren
no
Tongeren
no
Tongeren
no
Tongeren
no
Tongeren
no
Tongeren
no
Tongeren
no
Tongeren
no
Tongeren
no
Tongeren
no
Tongeren
no
Kortessem
no
Kortessem
no
Kortessem
no
Kortessem
no
Hoeselt
no
Hoeselt
no
Hoeselt
no
Hoeselt
no
Bilzen
no
Bilzen
no
Bilzen
no
B

no
Péruwelz
no
Péruwelz
no
Péruwelz
no
Péruwelz
no
Rumes
no
Rumes
no
Brunehaut
no
Brunehaut
no
Brunehaut
no
Brunehaut
no
Brunehaut
no
Brunehaut
no
Brunehaut
no
Brunehaut
no
Brunehaut
no
Antoing
no
Antoing
no
Antoing
no
Antoing
no
Antoing
no
Mouscron
no
La Louvière
no
Mouscron
no
Mouscron
no
Mouscron
no
Estaimpuis
no
Estaimpuis
no
Estaimpuis
no
Estaimpuis
no
Estaimpuis
no
Estaimpuis
no
Pecq
no
Pecq
no
Pecq
no
Pecq
no
Mont-de-l'Enclus
no
Mont-de-l'Enclus
no
Mont-de-l'Enclus
no
Mont-de-l'Enclus
no
Celles
no
Celles
no
Celles
no
Celles
no
Celles
no
Comines-Warneton
no
Comines-Warneton
no
Comines-Warneton
no
Comines-Warneton
no
Comines-Warneton
no
Comines-Warneton
no
Comines-Warneton
no
Comines-Warneton
no
Ath
no
Ath
no
Ath
no
Ath
no
Ath
no
Ath
no
Ath
no
Ath
no
Ath
no
Ath
no
Ath
no
Ath
no
Ath
no
Ath
no
Ath
no
Ath
no
Ath
no
Ath
no
Silly
no
Silly
no
Silly
no
Silly
no
Silly
no
Silly
no
Silly
no
Enghien
no
Enghien
no
Enghien
no
Enghien
no
Lessines
no
Lessines
no
Lessines
no
Lessines
no
Lessines


...

no
Les Bons Villers
no
Fleurus
no
Pont-à-Celles
no
Farciennes
no
Aiseau-Presles
no
Gerpinnes
no
Froidchapelle
no
Chimay
no
Sivry-Rance
no
Beaumont
no
Thuin
no
Lobbes
no
Erquelinnes
no
Merbes-le-Château
no
Momignies
no
Bastogne
no
Bastenaken
no
Martelange
no
Fauvillers
no
Vaux-sur-Sûre
no
Houffalize
no
Gouvy
no
Sainte-Ode
no
Bertogne
no
Vielsalm
no
Arlon
no
Aarlen
no
Attert
no
Habay
no
Tintigny
no
Étalle
no
Saint-Léger
no
Musson
no
Virton
no
Rouvroy
no
Meix-devant-Virton
no
Messancy
no
Aubange
no
Libramont-Chevigny
no
Chiny
no
Florenville
no
Bouillon
no
Neufchâteau
no
Paliseul
no
Léglise
no
Saint-Hubert
no
Bertrix
no
Herbeumont
no
Libin
no
Marche-en-Famenne
no
Wellin
no
Tellin
no
Daverdisse
no
Durbuy
no
Nassogne
no
Manhay
no
Tenneville
no
La Roche-en-Ardenne
no
Rendeux
no
Hotton
no
Érezée
no
Mons
no
Bergen
no
Quévy
no
Jurbise
no
Jurbeke
no
Soignies
no
Zinnik
no
Le Roeulx
no
Frameries
no
Braine-le-Comte
no
's-Gravenbrakel
no
La Louvière
no
Estinnes
no
Binche
no
Morlanwelz
no
Chapelle-lez

no
Sivry-Rance
no
Beaumont
no
Beaumont
no
Beaumont
no
Beaumont
no
Beaumont
no
Beaumont
no
Beaumont
no
Thuin
no
Thuin
no
Thuin
no
Thuin
no
Thuin
no
Thuin
no
Thuin
no
Lobbes
no
Lobbes
no
Lobbes
no
Erquelinnes
no
Erquelinnes
no
Erquelinnes
no
Erquelinnes
no
Erquelinnes
no
Merbes-le-Château
no
Merbes-le-Château
no
Merbes-le-Château
no
Momignies
no
Momignies
no
Momignies
no
Momignies
no
Momignies
no
Momignies
no
Bastogne
no
Bastogne
no
Bastogne
no
Bastogne
no
Fauvillers
no
Fauvillers
no
Vaux-sur-Sûre
no
Vaux-sur-Sûre
no
Vaux-sur-Sûre
no
Vaux-sur-Sûre
no
Vaux-sur-Sûre
no
Vaux-sur-Sûre
no
Houffalize
no
Houffalize
no
Houffalize
no
Houffalize
no
Houffalize
no
Houffalize
no
Gouvy
no
Gouvy
no
Gouvy
no
Gouvy
no
Gouvy
no
Sainte-Ode
no
Sainte-Ode
no
Sainte-Ode
no
Bertogne
no
Bertogne
no
Vielsalm
no
Vielsalm
no
Vielsalm
no
Arlon
no
Arlon
no
Arlon
no
Arlon
no
Arlon
no
Attert
no
Attert
no
Attert
no
Attert
no
Habay
no
Habay
no
Habay
no
Habay
no
Habay
no
Habay
no
Tintigny
no
Tintigny
no
Tintigny
no
Étall

Léglise
no
Saint-Hubert
no
Bertrix
no
Herbeumont
no
Libin
no
Marche-en-Famenne
no
Wellin
no
Tellin
no
Daverdisse
no
Durbuy
no
Nassogne
no
Manhay
no
Tenneville
no
La Roche-en-Ardenne
no
Rendeux
no
Hotton
no
Érezée
no
Mons
no
Bergen
no
Quévy
no
Jurbise
no
Jurbeke
no
Soignies
no
Zinnik
no
Le Roeulx
no
Frameries
no
Braine-le-Comte
no
's-Gravenbrakel
no
La Louvière
no
Estinnes
no
Binche
no
Morlanwelz
no
Chapelle-lez-Herlaimont
no
Manage
no
Seneffe
no
Écaussinnes
no
Boussu
no
Bernissart
no
Saint-Ghislain
no
Colfontaine
no
Hensies
no
Dour
no
Quiévrain
no
Honnelles
no
Quaregnon
no
Tournai
no
Doornik
no
Péruwelz
no
Rumes
no
Brunehaut
no
Antoing
no
Mouscron
no
Moeskroen
no
Estaimpuis
no
Steenput
no
Pecq
no
Mont-de-l'Enclus
no
Celles
no
Comines-Warneton
no
Komen-Waasten
no
Ath
no
Aat
no
Silly
no
Opzullik
no
Enghien
no
Edingen
no
Lessines
no
Lessen
no
Lens
no
Flobecq
no
Vloesberg
no
Ellezelles
no
Elzele
no
Leuze-en-Hainaut
no
Frasnes-lez-Anvaing
no
Brugelette
no
Chièvres
no
Beloeil
no
Brugge
no
Br

no
Lobbes
no
Lobbes
no
Erquelinnes
no
Erquelinnes
no
Erquelinnes
no
Erquelinnes
no
Erquelinnes
no
Merbes-le-Château
no
Merbes-le-Château
no
Merbes-le-Château
no
Momignies
no
Momignies
no
Momignies
no
Momignies
no
Momignies
no
Momignies
no
Bastogne
no
Bastogne
no
Bastogne
no
Bastogne
no
Fauvillers
no
Fauvillers
no
Vaux-sur-Sûre
no
Vaux-sur-Sûre
no
Vaux-sur-Sûre
no
Vaux-sur-Sûre
no
Vaux-sur-Sûre
no
Vaux-sur-Sûre
no
Houffalize
no
Houffalize
no
Houffalize
no
Houffalize
no
Houffalize
no
Houffalize
no
Gouvy
no
Gouvy
no
Gouvy
no
Gouvy
no
Gouvy
no
Sainte-Ode
no
Sainte-Ode
no
Sainte-Ode
no
Bertogne
no
Bertogne
no
Vielsalm
no
Vielsalm
no
Vielsalm
no
Arlon
no
Arlon
no
Arlon
no
Arlon
no
Arlon
no
Attert
no
Attert
no
Attert
no
Attert
no
Habay
no
Habay
no
Habay
no
Habay
no
Habay
no
Habay
no
Tintigny
no
Tintigny
no
Tintigny
no
Étalle
no
Étalle
no
Étalle
no
Étalle
no
Étalle
no
Saint-Léger
no
Saint-Léger
no
Musson
no
Virton
no
Virton
no
Virton
no
Virton
no
Virton
no
Rouvroy
no
Rouvroy
no
Rouvroy
no
Rouv

Gistel
no
Ichtegem
no
Jabbeke
no
Kortrijk
no
Courtrai
no
Kuurne
no
Harelbeke
no
Deerlijk
no
Zwevegem
no
Wevelgem
no
Anzegem
no
Avelgem
no
Spiere-Helkijn
no
Espierres-Helchin
no
Diksmuide
no
Dixmude
no
Kortemark
no
Nieuwpoort
no
Nieuport
no
Veurne
no
Furnes
no
Vleteren
no
Lo-Reninge
no
Houthulst
no
De Panne
no
La Panne
no
Koksijde
no
Koekelare
no
Alveringem
no
Tielt
no
Wielsbeke
no
Dentergem
no
Beernem
no
Pittem
no
Wingene
no
Ruiselede
no
Meulebeke
no
Ingelmunster
no
Oostrozebeke
no
Waregem
no
Roeselare
no
Roulers
no
Lichtervelde
no
Torhout
no
Hooglede
no
Staden
no
Ardooie
no
Lendelede
no
Izegem
no
Ledegem
no
Moorslede
no
Ieper
no
Ypres
no
Langemark-Poelkapelle
no
Menen
no
Menin
no
Wervik
no
Heuvelland
no
Mesen
no
Messines
no
Poperinge
no
Zonnebeke
no
Gent
no
Gand
no
Zelzate
no
Destelbergen
no
Lochristi
no
Melle
no
Sint-Niklaas
no
Saint-Nicolas
no
Beveren
no
Temse
no
Tamise
no
Kruibeke
no
Lokeren
no
Sint-Gillis-Waas
no
Moerbeke
no
Wachtebeke
no
Stekene
no
Dendermonde
no
Termonde
no
Hamm

In [10]:
df.to_csv('houses_filtered.csv', index = False)